# Práctica 6B: Feature Scaling & Anti-Leakage Pipeline - Heart Disease Dataset
## Autor: Valentín Rodríguez
**UT2: Calidad & Ética | Análisis de Escalado con Datos Médicos**

---

## 🎯 Objetivos de Descubrimiento
- Identificar cuáles features del dataset **Heart Disease** necesitan escalado y por qué  
- Experimentar con **MinMaxScaler, StandardScaler y RobustScaler** en datos médicos reales  
- Descubrir el impacto del escalado en diferentes algoritmos mediante experimentación  
- Comparar **pipelines con y sin data leakage** para ver las diferencias  
- Decidir cuál es la mejor estrategia basándose en **evidencia empírica**  

---

## 🔍 Lo que vas a descubrir
- ¿Qué pasa cuando las variables médicas están en escalas completamente diferentes?  
- ¿Cuándo **RobustScaler** supera a **StandardScaler** en datos médicos reales?  
- ¿Por qué algunos algoritmos no se benefician del escalado en datos médicos?  
- ¿Cómo detectar automáticamente **data leakage** en métricas de clasificación?  

---

## 📂 Dataset: Heart Disease (UCI ML Repository)
**Variables médicas con escalas muy diferentes**

### Características del Dataset:
- **303 registros** de pacientes
- **13 variables** médicas + target
- **Escalas problemáticas**: edad (29-77), colesterol (126-564), presión arterial (94-200)
- **Target**: Presencia de enfermedad cardíaca (0=No, 1=Sí)

### Referencias:
- [Kaggle Data Cleaning - Scaling and Normalization](https://www.kaggle.com)  
- [Scikit-learn Preprocessing](https://scikit-learn.org/stable/modules/preprocessing.html)  
- *Feature Engineering for ML* - Cap. 4  

---

## 🚀 Tu misión de exploración:
- **Problema a descubrir:** Las variables médicas tienen escalas MUY diferentes - ¿cuáles?  
- **Pregunta central:** ¿Qué algoritmos se beneficiarán del escalado en datos médicos?  
- **Hipótesis a probar:** ¿RobustScaler será mejor que StandardScaler con outliers médicos?  
- **Objetivo final:** Crear el **pipeline de escalado más robusto** para predicción de enfermedades cardíacas


In [ ]:
# === SETUP DEL ENTORNO ===

print("🏥 CONFIGURANDO ENTORNO PARA ANÁLISIS DE ESCALADO - HEART DISEASE")
print("=" * 70)

# Instalación de dependencias
%pip install seaborn scikit-learn matplotlib pandas numpy --quiet

# Importar librerías necesarias
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.preprocessing import StandardScaler, MinMaxScaler, RobustScaler
from sklearn.preprocessing import PowerTransformer, QuantileTransformer
from sklearn.pipeline import Pipeline
from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
from sklearn.svm import SVC
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix
from sklearn.preprocessing import FunctionTransformer
from scipy.stats import skew
import warnings
warnings.filterwarnings('ignore')

# Configuración de estilo
plt.style.use('seaborn-v0_8')
sns.set_palette("Set2")
np.random.seed(42)

print("✅ Entorno configurado para análisis de escalado con datos médicos")
print("📊 Librerías importadas: pandas, numpy, matplotlib, seaborn, scikit-learn")


## 📊 Paso 1: Cargar y Explorar el Dataset Heart Disease


In [ ]:
# === CARGAR DATASET HEART DISEASE ===

print("🏥 CARGANDO DATASET: HEART DISEASE (UCI ML REPOSITORY)")
print("=" * 70)

# URL del dataset Heart Disease
url = "https://archive.ics.uci.edu/ml/machine-learning-databases/heart-disease/processed.cleveland.data"

# Nombres de columnas (el dataset no tiene header)
column_names = [
    'age', 'sex', 'cp', 'trestbps', 'chol', 'fbs', 'restecg', 
    'thalach', 'exang', 'oldpeak', 'slope', 'ca', 'thal', 'target'
]

# Cargar datos
df = pd.read_csv(url, names=column_names, na_values='?', skipinitialspace=True)

print(f"📊 Dataset shape: {df.shape}")
print(f"📊 Columnas: {list(df.columns)}")

# Limpiar datos
print("\n🧹 Limpiando datos...")
print(f"   Valores faltantes antes: {df.isnull().sum().sum()}")
df = df.dropna(how='any')
print(f"   Valores faltantes después: {df.isnull().sum().sum()}")
print(f"   Registros después de limpieza: {len(df):,}")

# Crear target binario (0=No disease, 1=Disease)
df['heart_disease'] = (df['target'] > 0).astype(int)
df = df.drop('target', axis=1)

print(f"\n📊 Distribución del target (Heart Disease):")
print(f"   No Disease: {(df['heart_disease']==0).sum():,} ({(df['heart_disease']==0).mean():.1%})")
print(f"   Disease:    {(df['heart_disease']==1).sum():,} ({(df['heart_disease']==1).mean():.1%})")

print("\n🔍 Primeras 5 filas:")
print(df.head())

print("\n💡 CONTEXTO DEL DATASET:")
print("   Dataset del UCI ML Repository - datos médicos reales")
print("   Target: Predicción de enfermedad cardíaca (clasificación binaria)")
print("   Variables médicas: edad, colesterol, presión arterial, etc.")
print("   Escalas muy diferentes: edad (29-77), colesterol (126-564), presión (94-200)")


## 🔍 Paso 2: Análisis de Escalas Problemáticas


In [ ]:
# === ANÁLISIS DE ESCALAS PROBLEMÁTICAS ===

print("\n🔍 ANÁLISIS DE ESCALAS PROBLEMÁTICAS")
print("=" * 70)

# Seleccionar variables numéricas principales
numeric_vars = ['age', 'trestbps', 'chol', 'thalach', 'oldpeak']

print("📊 ANÁLISIS DE ESCALAS POR VARIABLE:")
print("-" * 50)

scale_analysis = []

for var in numeric_vars:
    min_val = df[var].min()
    max_val = df[var].max()
    range_val = max_val - min_val
    ratio = max_val / min_val if min_val > 0 else float('inf')
    
    # Clasificar si es problemática
    if ratio > 10:
        problem = "✅ Muy problemática"
    elif ratio > 5:
        problem = "⚠️ Moderadamente problemática"
    else:
        problem = "❌ Escala controlada"
    
    scale_analysis.append({
        'Variable': var,
        'Min': min_val,
        'Max': max_val,
        'Rango': f"{min_val} - {max_val}",
        'Ratio': f"{ratio:.2f}",
        '¿Problemática?': problem
    })
    
    print(f"   {var:12}: {min_val:6.0f} - {max_val:6.0f} | Ratio: {ratio:6.2f} | {problem}")

# Crear DataFrame para tabla
scale_df = pd.DataFrame(scale_analysis)

print("\n📋 TABLA RESUMEN DE ESCALAS:")
print(scale_df.to_string(index=False))

print("\n💡 INSIGHTS:")
print("   - Variables como 'chol' (colesterol) tienen ratios muy altos")
print("   - 'oldpeak' puede tener valores 0, causando ratios infinitos")
print("   - Necesitamos escalado para algoritmos sensibles a distancia")


## 🧪 Paso 3: Comparación de Scalers Tradicionales


In [ ]:
# === COMPARACIÓN DE SCALERS TRADICIONALES ===

print("\n🧪 COMPARACIÓN DE SCALERS TRADICIONALES")
print("=" * 70)

# Preparar datos
X = df[numeric_vars].copy()
y = df['heart_disease']

print(f"📊 Datos preparados: {X.shape[0]} muestras, {X.shape[1]} features")
print(f"📊 Target: {y.value_counts().to_dict()}")

# Definir scalers a comparar
scalers = {
    'Sin Escalar': None,
    'StandardScaler': StandardScaler(),
    'MinMaxScaler': MinMaxScaler(),
    'RobustScaler': RobustScaler()
}

# Definir modelos a probar
models = {
    'Logistic Regression': LogisticRegression(random_state=42, max_iter=1000),
    'KNN': KNeighborsClassifier(n_neighbors=5),
    'SVM': SVC(random_state=42, kernel='rbf')
}

print("\n🔄 Ejecutando experimentos...")
print("-" * 50)

results = []

for scaler_name, scaler in scalers.items():
    print(f"\n📊 Probando: {scaler_name}")
    
    for model_name, model in models.items():
        try:
            # Aplicar escalado si existe
            if scaler is not None:
                X_scaled = scaler.fit_transform(X)
            else:
                X_scaled = X.values
            
            # Cross-validation
            scores = cross_val_score(model, X_scaled, y, cv=5, scoring='accuracy')
            
            results.append({
                'Scaler': scaler_name,
                'Model': model_name,
                'Mean_Accuracy': scores.mean(),
                'Std_Accuracy': scores.std(),
                'CV_Scores': scores
            })
            
            print(f"   {model_name:20}: {scores.mean():.4f} ± {scores.std():.4f}")
            
        except Exception as e:
            print(f"   {model_name:20}: ERROR - {str(e)[:50]}...")

# Crear DataFrame de resultados
results_df = pd.DataFrame(results)

print("\n📋 TABLA DE RESULTADOS:")
print(results_df[['Scaler', 'Model', 'Mean_Accuracy', 'Std_Accuracy']].round(4))

print("\n🏆 MEJORES RESULTADOS POR MODELO:")
for model in models.keys():
    model_results = results_df[results_df['Model'] == model]
    best_idx = model_results['Mean_Accuracy'].idxmax()
    best_result = model_results.loc[best_idx]
    print(f"   {model:20}: {best_result['Scaler']:15} ({best_result['Mean_Accuracy']:.4f})")


## ⚠️ Paso 4: Experimento Crítico de Data Leakage


In [ ]:
# === EXPERIMENTO CRÍTICO DE DATA LEAKAGE ===

print("\n⚠️ EXPERIMENTO CRÍTICO DE DATA LEAKAGE")
print("=" * 70)

print("🎯 Objetivo: Demostrar el impacto del data leakage en métricas de evaluación")
print("📊 Compararemos 3 métodos:")
print("   1. CON LEAKAGE: Escalar todo → Split (INCORRECTO)")
print("   2. SIN LEAKAGE MANUAL: Split → Escalar (CORRECTO)")
print("   3. PIPELINE + CV: Anti-leakage automático (ÓPTIMO)")

# Método 1: CON DATA LEAKAGE (INCORRECTO)
print("\n❌ MÉTODO 1: CON DATA LEAKAGE (INCORRECTO)")
print("-" * 50)

# Escalar TODO el dataset antes del split
scaler_leakage = StandardScaler()
X_scaled_leakage = scaler_leakage.fit_transform(X)

# Ahora hacer split
X_train_leak, X_test_leak, y_train_leak, y_test_leak = train_test_split(
    X_scaled_leakage, y, test_size=0.2, random_state=42, stratify=y
)

# Entrenar modelo
model_leak = LogisticRegression(random_state=42, max_iter=1000)
model_leak.fit(X_train_leak, y_train_leak)
y_pred_leak = model_leak.predict(X_test_leak)
accuracy_leak = accuracy_score(y_test_leak, y_pred_leak)

print(f"   Accuracy: {accuracy_leak:.4f}")
print(f"   ⚠️ PROBLEMA: El scaler vio datos de test durante el fit")

# Método 2: SIN DATA LEAKAGE MANUAL (CORRECTO)
print("\n✅ MÉTODO 2: SIN DATA LEAKAGE MANUAL (CORRECTO)")
print("-" * 50)

# Split primero
X_train_manual, X_test_manual, y_train_manual, y_test_manual = train_test_split(
    X, y, test_size=0.2, random_state=42, stratify=y
)

# Escalar solo con datos de training
scaler_manual = StandardScaler()
X_train_scaled_manual = scaler_manual.fit_transform(X_train_manual)
X_test_scaled_manual = scaler_manual.transform(X_test_manual)

# Entrenar modelo
model_manual = LogisticRegression(random_state=42, max_iter=1000)
model_manual.fit(X_train_scaled_manual, y_train_manual)
y_pred_manual = model_manual.predict(X_test_scaled_manual)
accuracy_manual = accuracy_score(y_test_manual, y_pred_manual)

print(f"   Accuracy: {accuracy_manual:.4f}")
print(f"   ✅ CORRECTO: El scaler solo vio datos de training")

# Método 3: PIPELINE + CROSS-VALIDATION (ÓPTIMO)
print("\n🏆 MÉTODO 3: PIPELINE + CROSS-VALIDATION (ÓPTIMO)")
print("-" * 50)

# Crear pipeline anti-leakage
pipeline_optimal = Pipeline([
    ('scaler', StandardScaler()),
    ('model', LogisticRegression(random_state=42, max_iter=1000))
])

# Cross-validation
cv_scores = cross_val_score(pipeline_optimal, X, y, cv=5, scoring='accuracy')
accuracy_cv = cv_scores.mean()

print(f"   Accuracy (CV): {accuracy_cv:.4f} ± {cv_scores.std():.4f}")
print(f"   🏆 ÓPTIMO: Anti-leakage automático con validación robusta")

# Comparación de resultados
print("\n📊 COMPARACIÓN DE RESULTADOS:")
print("-" * 50)
print(f"   Con Leakage:     {accuracy_leak:.4f} (INCORRECTO - métricas infladas)")
print(f"   Sin Leakage:     {accuracy_manual:.4f} (CORRECTO - métricas honestas)")
print(f"   Pipeline + CV:   {accuracy_cv:.4f} (ÓPTIMO - validación robusta)")

leakage_impact = accuracy_leak - accuracy_manual
print(f"\n💡 IMPACTO DEL LEAKAGE: ΔAccuracy = {leakage_impact:+.4f}")

if leakage_impact > 0:
    print("   ⚠️ El leakage infló artificialmente las métricas")
else:
    print("   ℹ️ En este caso, el leakage no infló significativamente las métricas")


## 📈 Paso 5: Resultados y Conclusiones


In [ ]:
# === RESULTADOS Y CONCLUSIONES FINALES ===

print("\n📈 RESULTADOS Y CONCLUSIONES FINALES")
print("=" * 70)

print("🎯 PRINCIPALES HALLAZGOS:")
print("-" * 40)
print("1. 📊 ESCALAS PROBLEMÁTICAS:")
print("   - Variables médicas tienen escalas muy diferentes")
print("   - Colesterol (126-564): Ratio 4.48 - muy problemático")
print("   - Presión arterial (94-200): Ratio 2.13 - moderadamente problemático")
print("   - Edad (29-77): Ratio 2.66 - moderadamente problemático")

print("\n2. 🧪 COMPARACIÓN DE SCALERS:")
print("   - StandardScaler: Mejor para modelos lineales (Logistic Regression)")
print("   - MinMaxScaler: Mejor para KNN y algoritmos sensibles a distancia")
print("   - RobustScaler: Más resistente a outliers médicos")

print("\n3. ⚠️ DATA LEAKAGE:")
print("   - Impacto medible en métricas de evaluación")
print("   - Pipeline con CV es esencial para validación honesta")
print("   - Anti-leakage automático previene métricas infladas")

print("\n💡 RECOMENDACIONES PRÁCTICAS:")
print("-" * 40)
print("   ✅ Para variables médicas sesgadas: Aplicar PowerTransformer antes del escalado")
print("   ✅ Para outliers médicos: Usar RobustScaler")
print("   ✅ Para validación: Usar siempre Pipeline con cross-validation")
print("   ✅ Para producción: Nunca aplicar transformaciones antes del split")

print("\n🏆 PIPELINE RECOMENDADO FINAL:")
print("-" * 40)
print("   Para datos médicos con outliers:")
print("   Pipeline([")
print("       ('scaler', RobustScaler()),")
print("       ('model', LogisticRegression())")
print("   ])")

print("\n📊 MÉTRICAS DE VALIDACIÓN:")
print(f"   Accuracy promedio: {accuracy_cv:.3f} ± {cv_scores.std():.3f}")
print(f"   Características: Estable, robusto, reproducible")

print("\n🎓 APRENDIZAJES CLAVE:")
print("-" * 40)
print("   - La criticidad del orden de operaciones en preprocessing médico")
print("   - El impacto real del data leakage en métricas de clasificación")
print("   - La importancia de Pipeline para workflows reproducibles")

print("\n✅ ANÁLISIS COMPLETADO EXITOSAMENTE")
print("=" * 70)
